<a href="https://colab.research.google.com/github/sanjaykshetri/springboard_HW/blob/master/Copy_of_meteorites.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## YData Profiling: NASA Meteorites example
Source of data: https://data.nasa.gov/docs/legacy/meteorite_landings/Meteorite_Landings.csv

The autoreload instruction reloads modules automatically before code execution, which is helpful for the update below.

Make sure that we have the latest version of pandas-profiling.

In [2]:
import sys

!{sys.executable} -m pip install -U ydata-profiling[notebook]
!pip install jupyter-contrib-nbextensions
!jupyter nbextension enable --py widgetsnbextension

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 296.5/296.5 kB 23.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 97.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 679.7/679.7 kB 46.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 37.3/37.3 MB 54.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 105.4/105.4 kB 10.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 399.3/399.3 kB 32.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.3/12.3 MB 111.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.3/43.3 kB 2.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 79.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 76.7/76.7 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.8/59.8 kB 5.5 MB/s eta 0:00:00
  Attempting uninstall: scipy
    Found existing 

You might want to restart the kernel now.

### Import libraries

In [3]:
from pathlib import Path

import numpy as np
import pandas as pd
import requests

import ydata_profiling
from ydata_profiling.utils.cache import cache_file

### Load and prepare example dataset
We add some fake variables for illustrating pandas-profiling capabilities

In [4]:
file_name = cache_file(
    "meteorites.csv",
    "https://data.nasa.gov/docs/legacy/meteorite_landings/Meteorite_Landings.csv",
)

df = pd.read_csv(file_name)

# Note: Pandas does not support dates before 1880, so we ignore these for this analysis
df["year"] = pd.to_datetime(df["year"], errors="coerce")

# Example: Constant variable
df["source"] = "NASA"

# Example: Boolean variable
df["boolean"] = np.random.choice([True, False], df.shape[0])

# Example: Mixed with base types
df["mixed"] = np.random.choice([1, "A"], df.shape[0])

# Example: Highly correlated variables
df["reclat_city"] = df["reclat"] + np.random.normal(scale=5, size=(len(df)))

# Example: Duplicate observations
duplicates_to_add = pd.DataFrame(df.iloc[0:10])
duplicates_to_add["name"] = duplicates_to_add["name"] + " copy"

df = pd.concat([df, duplicates_to_add], ignore_index=True)

In [5]:
df.head()

name   id nametype     recclass  mass (g)  fall  \
0    Aachen    1    Valid           L5      21.0  Fell   
1    Aarhus    2    Valid           H6     720.0  Fell   
2      Abee    6    Valid          EH4  107000.0  Fell   
3  Acapulco   10    Valid  Acapulcoite    1914.0  Fell   
4   Achiras  370    Valid           L6     780.0  Fell   

                           year    reclat    reclong           GeoLocation  \
0 1970-01-01 00:00:00.000001880  50.77500    6.08333     (50.775, 6.08333)   
1 1970-01-01 00:00:00.000001951  56.18333   10.23333  (56.18333, 10.23333)   
2 1970-01-01 00:00:00.000001952  54.21667 -113.00000    (54.21667, -113.0)   
3 1970-01-01 00:00:00.000001976  16.88333  -99.90000     (16.88333, -99.9)   
4 1970-01-01 00:00:00.000001902 -33.16667  -64.95000   (-33.16667, -64.95)   

  source  boolean mixed  reclat_city  
0   NASA    False     1    48.612275  
1   NASA    False     A    49.315957  
2   NASA     True     1    43.681403  
3   NASA     True     1     9.547757  
4   NASA    False     1   -28.265059

### Inline report without saving object

In [6]:
report = df.profile_report(
    sort=None, html={"style": {"full_width": True}}, progress_bar=False
)
report

100%|██████████| 14/14 [00:01<00:00,  7.57it/s]


### Save report to file

In [7]:
profile_report = df.profile_report(html={"style": {"full_width": True}})
profile_report.to_file("/tmp/example.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


 29%|██▊       | 4/14 [00:00<00:01,  6.75it/s]/usr/local/lib/python3.12/dist-packages/ydata_profiling/model/pandas/describe_date_pandas.py:57: UserWarning: Discarding nonzero nanoseconds in conversion.
  "min": pd.Timestamp.to_pydatetime(series.min()),
/usr/local/lib/python3.12/dist-packages/ydata_profiling/model/pandas/describe_date_pandas.py:58: UserWarning: Discarding nonzero nanoseconds in conversion.
  "max": pd.Timestamp.to_pydatetime(series.max()),

100%|██████████| 14/14 [00:02<00:00,  6.27it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

### More analysis (Unicode) and Print existing ProfileReport object inline

In [8]:
profile_report = df.profile_report(
    explorative=True, html={"style": {"full_width": True}}
)
profile_report

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]


100%|██████████| 14/14 [00:02<00:00,  5.57it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Notebook Widgets

In [9]:
profile_report.to_widgets()

/usr/local/lib/python3.12/dist-packages/ydata_profiling/profile_report.py:535: UserWarning: Ipywidgets is not yet fully supported on Google Colab (https://github.com/googlecolab/colabtools/issues/60).As an alternative, you can use the HTML report. See the documentation for more information.
  warnings.warn(


Render widgets:   0%|          | 0/1 [00:00<?, ?it/s]

ValueError: ('widget type not understood', 'overview_tabs')